In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd

# Triskele
import sys
from pathlib import Path
triskele_path = Path('../triskele/python')
sys.path.append(str(triskele_path.resolve()))
import triskele

In [ ]:
fs = np.array([16,3]) * 2  # Figure Size

# Load ground truth

In [ ]:
gt = triskele.read('../Data/ground_truth/2018_IEEE_GRSS_DFC_GT_TR.tif')

In [ ]:
plt.figure(figsize=fs)
plt.imshow(gt, cmap=plt.get_cmap('GnBu'))
plt.colorbar()
plt.show()

In [ ]:
count = np.unique(gt, return_counts=True)
lbl = pd.read_csv('../labels.csv', index_col=0)
lbl['Count'] = count[1]
lbl

In [ ]:
plt.bar(*count, log=True)
plt.xticks(lbl.index.values,lbl['label'], rotation=90)
plt.show()

plt.bar(count[0][1:], count[1][1:])
plt.xticks(lbl.index.values[1:], lbl['label'][1:], rotation=90)
plt.show()

# Split data

Create a filter raster `split` with values:

- `0` No Data
- `1` Train
- `2` Test

In [ ]:
train_part = .9

split = np.zeros_like(gt)

for lbli, lblc in zip(count[0][1:], count[1][1:]):
    treshold = int(lblc * train_part)
    #print('lbli:{}, count:{}, train:{}'.format(lbli, lblc, treshold))
    f = np.nonzero(gt == lbli)
    split[f[0][:treshold], f[1][:treshold]] = 1
    split[f[0][treshold:], f[1][treshold:]] = 2
    
plt.figure(figsize=fs)
plt.imshow(split)
#plt.imshow(split * (gt==1))
plt.show()

## First Semantic Cross Validation Generator Prototype

**WORK IN PROGRESS** you 'll have fun

In [ ]:
nb_split = 5

def semantic_cvg(gt, nb_split, step=0):
    test_part = 1 / nb_split

    split = np.zeros_like(gt)

    for lbli, lblc in zip(count[0][1:], count[1][1:]):
        treshold = int(lblc * test_part)
        #print('lbli:{}, count:{}, train:{}'.format(lbli, lblc, treshold))
        f = np.nonzero(gt == lbli)
        t_int, t_ext = treshold * step, treshold * (step + 1)
        split[f[0], f[1]] = 1
        split[f[0][t_int:t_ext], f[1][t_int:t_ext]] = 2

    return split

fig, axs = plt.subplots(nb_split, figsize=fs * nb_split)

for i in range(nb_split):
    split = semantic_cvg(gt, nb_split, i)

    axs[i].imshow(split)
    axs[i].set_title(i)
#plt.imshow(split * (gt==1))
plt.savefig('../Res/cross_valid_split_{}.png'.format(nb_split))
plt.show()

# Metaclasses 

In [ ]:
metaclasses_A = {'Grass': [1, 2, 3],
                 'Trees': [4, 5],
                 'Hard Ground': [6, 17],
                 'Water': [7],
                 'Buildings': [8, 9],
                 'Roads': [10, 11, 12, 13, 14, 16],
                 'Railways': [15],
                 'Cars': [18],
                 'Trains': [19],
                 'Stadium': [20]}

In [ ]:
plt.figure(figsize=fs)
plt.imshow(np.isin(gt, metaclasses_A['Roads']))
plt.show()

In [ ]:
plt.figure(figsize=fs)
plt.imshow(gt * np.isin(gt, metaclasses_A['Roads']))
plt.show()

## Database-style

In [ ]:
dfc_lbl  = pd.read_csv('../labels.csv')
meta_idx = pd.read_csv('../metaclass_indexes.csv')
meta_lbl = pd.read_csv('../metaclass_labels.csv')

In [ ]:
dfc_meta_view = pd.merge(dfc_lbl, meta_idx)
all_meta_view = pd.merge(dfc_meta_view, meta_lbl)
all_meta_view

In [ ]:
np.array(all_meta_view[all_meta_view['metaclass_label'] == 'Roads']['index'])

In [ ]:
plt.figure(figsize=fs)
plt.imshow(gt * np.isin(gt, np.array(all_meta_view[all_meta_view['metaclass_label'] == 'Roads']['index'])))
plt.show()

In [ ]:
count = np.unique(gt, return_counts=True)
df_count = pd.DataFrame(np.array(count).T, columns=['index', 'count'])
df_count.head()

In [ ]:
import seaborn as sns

df_tmp = meta_idx.merge(df_count).merge(meta_lbl).merge(dfc_lbl).drop(index=0)
display(df_tmp.head())

g = sns.barplot(data=df_tmp, x='label', y='count')
plt.xticks(rotation=80)
plt.show()

In [ ]:
meta_count_view = pd.merge(meta_idx, df_count)
display(meta_count_view.head())
meta_count_view.drop('index', 1, inplace=True)
meta_count_view = meta_count_view.groupby('metaclass_index', as_index=False).sum()
display(meta_count_view.head())

pd.merge(meta_lbl, meta_count_view)

In [ ]:
meta_index = np.array(meta_idx['metaclass_index'])

In [ ]:
plt.figure(figsize=fs)
plt.imshow(meta_index[gt])
plt.colorbar()
plt.show()